<a href="https://colab.research.google.com/github/Danielmejiava/danielmejiava/blob/main/PortfolioOptimization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<p style="text-align:center">
    <a href="https://www.itm.edu.co" target="_blank">
    <img src="https://www.itm.edu.co//wp-content/uploads/2021/08/logo-redes.png" width="200" alt="Skills Network Logo"  />
    </a>
</p>



# Work on Portfolio Optimization



## Integrantes:



*   Lizeth Giraldo
*   Perla Vanegas
*   Carlos Arturo
*   Daniel Mejía

## Objective:
The objective is to maximize the return of a stock portfolio.

## Stocks:

*   [Ecopetrol](https://www.ecopetrol.com.co/wps/portal)
*   [Airbus SE](https://www.airbus.com/en)
*   [American Airlines](https://www.aa.com/homePage.do?locale=es_MX)
*   [InBev SA](https://www.ab-inbev.com/)
*   [Simon Property Group](https://www.simon.com/)
*   [The Walt Disney Company](https://thewaltdisneycompany.com/)
*   [Amazon.com](https://www.amazon.com/)
*   [United Parcel Service](https://www.ups.com/co/es/Home.page)
*   [Netflix](https://www.netflix.com/co/)



In [2]:
# Install necessary libraries (if you haven't already installed them)
!pip install yfinance
!pip install plotly
!pip install chart-studio

# Importing libraries for data collection and analysis
import yfinance as yf             # For financial data collection
import numpy as np                # For numerical operations
import pandas as pd               # For data manipulation
from datetime import datetime     # For working with dates
import pandas_datareader.data as web  # For financial data from various sources

# Visualization libraries
import matplotlib.pyplot as plt    # For basic plotting
import seaborn as sns             # For advanced visualizations
import plotly.express as px       # For interactive visualizations
import plotly.graph_objects as go # For more advanced interactive visualizations
from plotly.subplots import make_subplots  # For creating subplots in Plotly
import plotly.figure_factory as ff  # For creating specialized figures

# Other useful libraries
from scipy import stats            # For statistical analysis
from tabulate import tabulate      # For displaying tables in a pretty format

# If you need to check your libraries:
print("Libraries imported successfully!")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.4/64.4 kB 667.1 kB/s eta 0:00:00
Libraries imported successfully!


In [3]:
# Create a Ticker object for Microsoft (MSFT)
msft = yf.Ticker("MSFT")

# Fetch and print the information for MSFT
print(msft.info)

{'address1': 'One Microsoft Way', 'city': 'Redmond', 'state': 'WA', 'zip': '98052-6399', 'country': 'United States', 'phone': '425 882 8080', 'website': 'https://www.microsoft.com', 'industry': 'Software - Infrastructure', 'industryKey': 'software-infrastructure', 'industryDisp': 'Software - Infrastructure', 'sector': 'Technology', 'sectorKey': 'technology', 'sectorDisp': 'Technology', 'longBusinessSummary': "Microsoft Corporation develops and supports software, services, devices, and solutions worldwide. The company's Productivity and Business Processes segment offers Microsoft 365 Commercial, Enterprise Mobility + Security, Windows Commercial, Power BI, Exchange, SharePoint, Microsoft Teams, Security and Compliance, and Copilot; Microsoft 365 Commercial products, such as Windows Commercial on-premises and Office licensed services; Microsoft 365 Consumer products and cloud services, such as Microsoft 365 Consumer subscriptions, Office licensed on-premises, and other consumer services;

In [4]:
# Define tickers (including 'USDCOP=X' for exchange rate)
tickers = ['AAL', 'ABI.BR', 'AIR.PA', 'AMZN', 'DIS', 'ECOPETROL.CL', 'NFLX', 'SPG', 'UPS', 'USDCOP=X']

# Download adjusted close prices
df = yf.download(tickers, start="2017-01-01", end="2025-05-01", auto_adjust=True)

# Step 1: Flatten multi-level columns if necessary (flattening 'Close' column levels)
if isinstance(df.columns, pd.MultiIndex):
    df.columns = [' '.join(col).strip() for col in df.columns.to_flat_index()]

# Step 2: Reset the index to bring 'Date' as a normal column
df = df.reset_index()

# Step 3: Forward fill NaN values in the entire DataFrame (important for missing values)
df = df.fillna(method='ffill')

df = df.replace(0, method='ffill')

df.head()
print(df.columns)



[*********************100%***********************]  10 of 10 completed

Index(['Date', 'Close AAL', 'Close ABI.BR', 'Close AIR.PA', 'Close AMZN',
       'Close DIS', 'Close ECOPETROL.CL', 'Close NFLX', 'Close SPG',
       'Close UPS', 'Close USDCOP=X', 'High AAL', 'High ABI.BR', 'High AIR.PA',
       'High AMZN', 'High DIS', 'High ECOPETROL.CL', 'High NFLX', 'High SPG',
       'High UPS', 'High USDCOP=X', 'Low AAL', 'Low ABI.BR', 'Low AIR.PA',
       'Low AMZN', 'Low DIS', 'Low ECOPETROL.CL', 'Low NFLX', 'Low SPG',
       'Low UPS', 'Low USDCOP=X', 'Open AAL', 'Open ABI.BR', 'Open AIR.PA',
       'Open AMZN', 'Open DIS', 'Open ECOPETROL.CL', 'Open NFLX', 'Open SPG',
       'Open UPS', 'Open USDCOP=X', 'Volume AAL', 'Volume ABI.BR',
       'Volume AIR.PA', 'Volume AMZN', 'Volume DIS', 'Volume ECOPETROL.CL',
       'Volume NFLX', 'Volume SPG', 'Volume UPS', 'Volume USDCOP=X'],
      dtype='object')



/tmp/ipython-input-1701395172.py:15: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df = df.fillna(method='ffill')
/tmp/ipython-input-1701395172.py:17: FutureWarning: The 'method' keyword in DataFrame.replace is deprecated and will be removed in a future version.
  df = df.replace(0, method='ffill')


In [5]:

# Step 4: Identify the 'Close' columns (those with 'Close' in their name)
close_columns = [col for col in df.columns if 'Close' in col]

In [6]:
# Step 5: Apply the natural logarithm (np.log) to each 'Close' column (logarithmic returns)
for col in close_columns:
    df[f'LogVariation {col}'] = np.log(df[col] / df[col].shift(1))
df.head()


Date  Close AAL  Close ABI.BR  Close AIR.PA  Close AMZN   Close DIS  \
0 2017-01-02        NaN     85.444778     56.623672         NaN         NaN   
1 2017-01-03  44.741226     84.684143     57.236599   37.683498   99.918640   
2 2017-01-04  45.127766     84.895424     57.146465   37.859001  101.199646   
3 2017-01-05  44.345028     85.402512     58.228100   39.022499  101.143135   
4 2017-01-06  44.654255     84.937683     58.714828   39.799500  102.650200   

   Close ECOPETROL.CL  Close NFLX   Close SPG  Close UPS  ...  \
0          673.954102         NaN         NaN        NaN  ...   
1          683.865112  127.489998  116.153877  85.239296  ...   
2          693.776123  129.410004  117.082535  85.261497  ...   
3          701.209534  131.809998  117.286102  85.305962  ...   
4          691.298584  131.070007  118.831680  85.476311  ...   

   LogVariation Close AAL  LogVariation Close ABI.BR  \
0                     NaN                        NaN   
1                     NaN                  -0.008942   
2                0.008602                   0.002492   
3               -0.017497                   0.005955   
4                0.006949                  -0.005458   

   LogVariation Close AIR.PA  LogVariation Close AMZN  LogVariation Close DIS  \
0                        NaN                      NaN                     NaN   
1                   0.010766                      NaN                     NaN   
2                  -0.001576                 0.004646                0.012739   
3                   0.018751                 0.030270               -0.000559   
4                   0.008324                 0.019716                0.014790   

   LogVariation Close ECOPETROL.CL  LogVariation Close NFLX  \
0                              NaN                      NaN   
1                         0.014599                      NaN   
2                         0.014389                 0.014948   
3                         0.010657                 0.018376   
4                        -0.014235                -0.005630   

   LogVariation Close SPG  LogVariation Close UPS  LogVariation Close USDCOP=X  
0                     NaN                     NaN                          NaN  
1                     NaN                     NaN                    -0.002167  
2                0.007963                0.000260                    -0.011761  
3                0.001737                0.000521                    -0.008644  
4                0.013092                0.001995                     0.002349  

[5 rows x 61 columns]

In [7]:
# Step 6: Calculate the log variation for 'USDCOP=X' (the exchange rate)
df['LogVariation USDCOP=X'] = np.log(df['Close USDCOP=X'] / df['Close USDCOP=X'].shift(1))
df.head()


Date  Close AAL  Close ABI.BR  Close AIR.PA  Close AMZN   Close DIS  \
0 2017-01-02        NaN     85.444778     56.623672         NaN         NaN   
1 2017-01-03  44.741226     84.684143     57.236599   37.683498   99.918640   
2 2017-01-04  45.127766     84.895424     57.146465   37.859001  101.199646   
3 2017-01-05  44.345028     85.402512     58.228100   39.022499  101.143135   
4 2017-01-06  44.654255     84.937683     58.714828   39.799500  102.650200   

   Close ECOPETROL.CL  Close NFLX   Close SPG  Close UPS  ...  \
0          673.954102         NaN         NaN        NaN  ...   
1          683.865112  127.489998  116.153877  85.239296  ...   
2          693.776123  129.410004  117.082535  85.261497  ...   
3          701.209534  131.809998  117.286102  85.305962  ...   
4          691.298584  131.070007  118.831680  85.476311  ...   

   LogVariation Close ABI.BR  LogVariation Close AIR.PA  \
0                        NaN                        NaN   
1                  -0.008942                   0.010766   
2                   0.002492                  -0.001576   
3                   0.005955                   0.018751   
4                  -0.005458                   0.008324   

   LogVariation Close AMZN  LogVariation Close DIS  \
0                      NaN                     NaN   
1                      NaN                     NaN   
2                 0.004646                0.012739   
3                 0.030270               -0.000559   
4                 0.019716                0.014790   

   LogVariation Close ECOPETROL.CL  LogVariation Close NFLX  \
0                              NaN                      NaN   
1                         0.014599                      NaN   
2                         0.014389                 0.014948   
3                         0.010657                 0.018376   
4                        -0.014235                -0.005630   

   LogVariation Close SPG  LogVariation Close UPS  \
0                     NaN                     NaN   
1                     NaN                     NaN   
2                0.007963                0.000260   
3                0.001737                0.000521   
4                0.013092                0.001995   

   LogVariation Close USDCOP=X  LogVariation USDCOP=X  
0                          NaN                    NaN  
1                    -0.002167              -0.002167  
2                    -0.011761              -0.011761  
3                    -0.008644              -0.008644  
4                     0.002349               0.002349  

[5 rows x 62 columns]

In [8]:
#from google.colab import sheets
#sheet = sheets.InteractiveSheet(df=df)

In [9]:
# Step 6: Apply the natural logarithm to 'USDCOP=X' column (logarithmic return)
df['LogVariation USDCOP=X'] = np.log(df['Close USDCOP=X'] / df['Close USDCOP=X'].shift(1))

df.head()


Date  Close AAL  Close ABI.BR  Close AIR.PA  Close AMZN   Close DIS  \
0 2017-01-02        NaN     85.444778     56.623672         NaN         NaN   
1 2017-01-03  44.741226     84.684143     57.236599   37.683498   99.918640   
2 2017-01-04  45.127766     84.895424     57.146465   37.859001  101.199646   
3 2017-01-05  44.345028     85.402512     58.228100   39.022499  101.143135   
4 2017-01-06  44.654255     84.937683     58.714828   39.799500  102.650200   

   Close ECOPETROL.CL  Close NFLX   Close SPG  Close UPS  ...  \
0          673.954102         NaN         NaN        NaN  ...   
1          683.865112  127.489998  116.153877  85.239296  ...   
2          693.776123  129.410004  117.082535  85.261497  ...   
3          701.209534  131.809998  117.286102  85.305962  ...   
4          691.298584  131.070007  118.831680  85.476311  ...   

   LogVariation Close ABI.BR  LogVariation Close AIR.PA  \
0                        NaN                        NaN   
1                  -0.008942                   0.010766   
2                   0.002492                  -0.001576   
3                   0.005955                   0.018751   
4                  -0.005458                   0.008324   

   LogVariation Close AMZN  LogVariation Close DIS  \
0                      NaN                     NaN   
1                      NaN                     NaN   
2                 0.004646                0.012739   
3                 0.030270               -0.000559   
4                 0.019716                0.014790   

   LogVariation Close ECOPETROL.CL  LogVariation Close NFLX  \
0                              NaN                      NaN   
1                         0.014599                      NaN   
2                         0.014389                 0.014948   
3                         0.010657                 0.018376   
4                        -0.014235                -0.005630   

   LogVariation Close SPG  LogVariation Close UPS  \
0                     NaN                     NaN   
1                     NaN                     NaN   
2                0.007963                0.000260   
3                0.001737                0.000521   
4                0.013092                0.001995   

   LogVariation Close USDCOP=X  LogVariation USDCOP=X  
0                          NaN                    NaN  
1                    -0.002167              -0.002167  
2                    -0.011761              -0.011761  
3                    -0.008644              -0.008644  
4                     0.002349               0.002349  

[5 rows x 62 columns]

In [10]:
# Step 6: Apply the formula for logarithmic adjustment for each stock using 'USDCOP=X' as the adjustment factor
for col in close_columns:
    df[f'LogVariationAjust {col}'] = (1 + df[f'LogVariation {col}']) * (1 + df['LogVariation USDCOP=X']) - 1
df.head()

Date  Close AAL  Close ABI.BR  Close AIR.PA  Close AMZN   Close DIS  \
0 2017-01-02        NaN     85.444778     56.623672         NaN         NaN   
1 2017-01-03  44.741226     84.684143     57.236599   37.683498   99.918640   
2 2017-01-04  45.127766     84.895424     57.146465   37.859001  101.199646   
3 2017-01-05  44.345028     85.402512     58.228100   39.022499  101.143135   
4 2017-01-06  44.654255     84.937683     58.714828   39.799500  102.650200   

   Close ECOPETROL.CL  Close NFLX   Close SPG  Close UPS  ...  \
0          673.954102         NaN         NaN        NaN  ...   
1          683.865112  127.489998  116.153877  85.239296  ...   
2          693.776123  129.410004  117.082535  85.261497  ...   
3          701.209534  131.809998  117.286102  85.305962  ...   
4          691.298584  131.070007  118.831680  85.476311  ...   

   LogVariationAjust Close AAL  LogVariationAjust Close ABI.BR  \
0                          NaN                             NaN   
1                          NaN                       -0.011089   
2                    -0.003260                       -0.009299   
3                    -0.025990                       -0.002740   
4                     0.009315                       -0.003121   

   LogVariationAjust Close AIR.PA  LogVariationAjust Close AMZN  \
0                             NaN                           NaN   
1                        0.008576                           NaN   
2                       -0.013318                     -0.007169   
3                        0.009944                      0.021364   
4                        0.010693                      0.022111   

   LogVariationAjust Close DIS  LogVariationAjust Close ECOPETROL.CL  \
0                          NaN                                   NaN   
1                          NaN                              0.012400   
2                     0.000828                              0.002458   
3                    -0.009198                              0.001921   
4                     0.017174                             -0.011919   

   LogVariationAjust Close NFLX  LogVariationAjust Close SPG  \
0                           NaN                          NaN   
1                           NaN                          NaN   
2                      0.003011                    -0.003891   
3                      0.009573                    -0.006922   
4                     -0.003294                     0.015472   

   LogVariationAjust Close UPS  LogVariationAjust Close USDCOP=X  
0                          NaN                               NaN  
1                          NaN                         -0.004329  
2                    -0.011504                         -0.023384  
3                    -0.008127                         -0.017214  
4                     0.004349                          0.004704  

[5 rows x 72 columns]

In [11]:
# Step 1: Melt the dataframe to long-form for plotting
# Melt the DataFrame to include both the 'LogVariation' and 'LogVariationAjust' columns
df_long = df.melt(id_vars=['Date'], value_vars=[f'LogVariation {col}' for col in close_columns] + [f'LogVariationAjust {col}' for col in close_columns],
                  var_name='Stock Type', value_name='Logarithmic Variation')

# Step 2: Create the plot using Plotly Express
fig = px.line(df_long, x='Date', y='Logarithmic Variation', color='Stock Type', line_group='Stock Type', title="Stock Price Fluctuation")

# Step 3: Update layout with specific titles and formatting
fig.update_layout(
    xaxis_title="Date",
    yaxis_title="Logarithmic Variation",
    legend_title="Stock Type",
    font=dict(
        family="Courier New, monospace",
        size=10,
        color="black"
    )
)

# Step 4: Show the plot
fig.show()



In [12]:
# Step 1: Ensure that the DataFrame contains only adjusted log variation columns
# Identify the 'LogVariationAjust' columns (those with 'LogVariationAjust' in their name)
adjusted_columns = [col for col in df.columns if 'LogVariationAjust' in col]
VariationLog_numeric = df[adjusted_columns]

# Step 2: Calculate descriptive statistics for the adjusted log variation columns
statistic = VariationLog_numeric.describe()
resumenEstadistico = statistic.transpose()

# Step 3: Add new calculated columns for adjusted log variation only
# Calculate the annual return ('Annual Return') assuming 252 trading days
resumenEstadistico['Annual Return'] = ((1 + resumenEstadistico['mean']) ** 252 - 1)

# Calculate the volatility ('Volatility')
resumenEstadistico['Volatility'] = (resumenEstadistico['std']) * 252 ** (1/2)

# Calculate the efficiency ('Efficiency') as Annual Return / Volatility
resumenEstadistico['Efficiency'] = resumenEstadistico['Annual Return'] / resumenEstadistico['Volatility']

# Add custom 'Beta' values (these could come from a financial model, but we'll keep them static for now)
# Since the DataFrame is transposed, we need to repeat these values to match the number of stocks.
beta_values = [1.13, 1.70, 1.47, 1.13, 1.53, 1.25, 1.23, 1.11, 1.28, 1.31]
resumenEstadistico['Beta'] = beta_values

# Add custom 'PER' (Price-to-Earnings ratio) values
per_values = [2.88, 20.96, 0.0, 23.94, 19.67, 50.79, 79.38, 13.76, 24.03, 29.42]
resumenEstadistico['PER'] = per_values

# Add 'Weights' ('Ponderaciones'), assuming equal weight for each stock
weights_values = [0.1] * len(resumenEstadistico)
resumenEstadistico['Weights'] = weights_values

# Calculate 'Asset Return' as Annual Return * Weights
resumenEstadistico['Asset Return'] = resumenEstadistico['Annual Return'] * resumenEstadistico['Weights']

# Step 4: Show the result (Transpose to make it easier to read)
resumenEstadistico.T




LogVariationAjust Close AAL  LogVariationAjust Close ABI.BR  \
count                          2170.000000                     2171.000000   
mean                             -0.000531                       -0.000028   
std                               0.034636                        0.020255   
min                              -0.305000                       -0.185961   
25%                              -0.016857                       -0.010388   
50%                              -0.000625                       -0.000237   
75%                               0.015259                        0.009880   
max                               0.333345                        0.165208   
Annual Return                    -0.125194                       -0.006921   
Volatility                        0.549823                        0.321534   
Efficiency                       -0.227698                       -0.021524   
Beta                              1.130000                        1.700000   
PER                               2.880000                       20.960000   
Weights                           0.100000                        0.100000   
Asset Return                     -0.012519                       -0.000692   

               LogVariationAjust Close AIR.PA  LogVariationAjust Close AMZN  \
count                             2171.000000                   2170.000000   
mean                                 0.000602                      0.000897   
std                                  0.024596                      0.023060   
min                                 -0.265751                     -0.149051   
25%                                 -0.011822                     -0.011371   
50%                                  0.000197                      0.000223   
75%                                  0.012483                      0.013365   
max                                  0.160636                      0.139271   
Annual Return                        0.163822                      0.253460   
Volatility                           0.390449                      0.366063   
Efficiency                           0.419573                      0.692395   
Beta                                 1.470000                      1.130000   
PER                                  0.000000                     23.940000   
Weights                              0.100000                      0.100000   
Asset Return                         0.016382                      0.025346   

               LogVariationAjust Close DIS  \
count                          2170.000000   
mean                              0.000120   
std                               0.021139   
min                              -0.163937   
25%                              -0.010511   
50%                              -0.000227   
75%                               0.010422   
max                               0.190402   
Annual Return                     0.030806   
Volatility                        0.335574   
Efficiency                        0.091800   
Beta                              1.530000   
PER                              19.670000   
Weights                           0.100000   
Asset Return                      0.003081   

               LogVariationAjust Close ECOPETROL.CL  \
count                                   2171.000000   
mean                                       0.000594   
std                                        0.025158   
min                                       -0.213699   
25%                                       -0.011061   
50%                                        0.000755   
75%                                        0.012180   
max                                        0.207074   
Annual Return                              0.161382   
Volatility                                 0.399366   
Efficiency                                 0.404095   
Beta                                       1.250000   
PER                                       50.7900

In [13]:
# Check the columns to ensure 'Renta EA' is present
print(resumenEstadistico.columns)


Index(['count', 'mean', 'std', 'min', '25%', '50%', '75%', 'max',
       'Annual Return', 'Volatility', 'Efficiency', 'Beta', 'PER', 'Weights',
       'Asset Return'],
      dtype='object')


In [14]:
# Step 1: Ensure that the Ponderaciones column is correctly added (assuming equal weight for each stock)
resumenEstadistico['Ponderaciones'] = [0.1] * len(resumenEstadistico)

# Step 2: Calculate Rentabilidad Activos (Asset Return) as Annual Return * Ponderaciones
# Use 'Annual Return' instead of 'Renta EA'
resumenEstadistico['Asset Return'] = resumenEstadistico['Annual Return'] * resumenEstadistico['Ponderaciones']

# Step 3: Calculate the total portfolio return by summing the 'Asset Return' column
portfolio_return = resumenEstadistico['Asset Return'].sum()

# Step 4: Print the total portfolio return
print("Total Portfolio Return:", portfolio_return)




Total Portfolio Return: 0.10618498497770433


In [15]:
# Step 1: Calculate the Sharpe Ratio
# Assuming a risk-free rate of 0% (you can adjust this as needed, e.g., 2% for treasury bills)
risk_free_rate = 0.0

# Calculate the annualized Sharpe Ratio (portfolio return / portfolio volatility)
sharpe_ratio = (portfolio_return - risk_free_rate) / resumenEstadistico['Volatility'].mean()

# Step 2: Display the Sharpe Ratio
print("Sharpe Ratio:", sharpe_ratio)


Sharpe Ratio: 0.2739401493495601


In [16]:
# Step 1: Select only the 'LogVariationAjust' columns for all stocks
adjusted_columns = [col for col in df.columns if 'LogVariationAjust' in col]

# Step 2: Melt the DataFrame to long format, using only the 'LogVariationAjust' columns
df_long = df[['Date'] + adjusted_columns].melt(id_vars=['Date'], var_name='Acciones', value_name='Logarithmic Variation')

# Step 3: Create the box plot for the 'Logarithmic Variation' of the 'LogVariationAjust' prices
fig = px.box(df_long, x='Acciones', y='Logarithmic Variation', title="Estadística Acciones (Logarithmic Variation Adjusted)")

# Step 4: Update layout with titles and formatting
fig.update_layout(
    xaxis_title="Acciones",  # Label for the x-axis (stocks)
    yaxis_title="Variación Logaritmica Ajustada",  # Label for the y-axis (adjusted logarithmic variation)
    legend_title="Acciones",  # Legend title (for stock names)
    font=dict(
        family="Courier New, monospace",  # Font for the labels and title
        size=10,  # Font size
        color="black"  # Font color
    )
)

# Step 5: Display the plot
fig.show()



In [17]:
# Step 1: Select only the 'LogVariationAjust' columns (adjusted log variations) and other numeric columns
adjusted_columns = [col for col in df.columns if 'LogVariationAjust' in col]

# Exclude the 'Date' column (which is non-numeric) and select numeric columns only
VariationLog_numeric = df[['Date'] + adjusted_columns].select_dtypes(include=['float64', 'int64'])

# Step 2: Calculate the covariance matrix for numeric columns
cov = VariationLog_numeric.cov()

# Step 3: Display the covariance matrix with better visualization using background gradient
cov.style.background_gradient(cmap='viridis')


In [18]:
# Adjust the covariance matrix for 252 trading days (annualize it)
cov_matrix_annualized = cov * 252

# Weights for each stock in the portfolio (assuming equal weights)
weights = np.array([0.1] * len(cov_matrix_annualized))

# Step 1: Calculate Portfolio Variance
portfolio_variance = np.dot(weights.T, np.dot(cov_matrix_annualized, weights))

# Step 2: Calculate Portfolio Volatility (square root of variance)
portfolio_volatility = np.sqrt(portfolio_variance)

# Step 3: Convert volatility to percentage format
portfolio_volatility_percent = str(round(portfolio_volatility * 100, 4)) + '%'

# Step 4: Calculate Efficiency (Risk-Return ratio)
# Assuming we use the average of the 'Annual Return' as a proxy for the portfolio return
average_annual_return = resumenEstadistico['Annual Return'].mean()

# Calculate Efficiency: Risk-Return ratio
efficiency = average_annual_return / portfolio_volatility

# Step 5: Display Results
print('Portfolio Risk: ', portfolio_volatility_percent, '%',
      '\nEfficiency: ', efficiency)



Portfolio Risk:  26.4086% % 
Efficiency:  0.4020854679868574


In [19]:
# Step 1: Select only the 'LogVariationAjust' columns
adjusted_columns = [col for col in df.columns if 'LogVariationAjust' in col]

# Step 2: Select only the numeric 'LogVariationAjust' columns (adjusted log variations)
df_numeric = df[['Date'] + adjusted_columns].select_dtypes(include=['float64', 'int64'])

# Step 3: Calculate the annualized return (mus) for each adjusted log variation column
annualized_returns = (1 + df_numeric.mean()) ** 252 - 1

# Step 4: Display the annualized returns
print("Annualized Returns (mus) for Adjusted Log Variations:")
print(annualized_returns)




Annualized Returns (mus) for Adjusted Log Variations:
LogVariationAjust Close AAL            -0.125194
LogVariationAjust Close ABI.BR         -0.006921
LogVariationAjust Close AIR.PA          0.163822
LogVariationAjust Close AMZN            0.253460
LogVariationAjust Close DIS             0.030806
LogVariationAjust Close ECOPETROL.CL    0.161382
LogVariationAjust Close NFLX            0.340417
LogVariationAjust Close SPG             0.079005
LogVariationAjust Close UPS             0.053217
LogVariationAjust Close USDCOP=X        0.111856
dtype: float64


In [20]:
import numpy as np
import pandas as pd
import plotly.express as px

# Assuming 'df', 'mus' (annualized returns), and 'cov' (covariance matrix) are already defined

# Step 1: Clean the asset names to remove prefixes like 'LogVariationAjust ', 'Close', etc.
cleaned_assets = [col.split(' ')[-1] for col in df.columns if 'LogVariationAjust' in col]

# Clean the asset names in 'mus' and 'cov'
mus.index = [col.split(' ')[-1] for col in mus.index]  # Clean 'mus' index names
cov.columns = [col.split(' ')[-1] for col in cov.columns]  # Clean 'cov' column names
cov.index = [col.split(' ')[-1] for col in cov.index]  # Clean 'cov' index names

# Step 2: Portfolio Simulation
n_assets = 5  # Number of assets in each portfolio
n_portfolios = 10000  # Number of portfolios to generate
mean_variance_pairs = []  # List to store mean-variance pairs for plotting

# Set a random seed for reproducibility
np.random.seed(75)

# Step 3: Generate random portfolios and calculate their returns and variances
for i in range(n_portfolios):
    # Step 4: Select n_assets random assets from the cleaned asset names (stock symbols)
    assets = np.random.choice(cleaned_assets, n_assets, replace=False)

    # Step 5: Choose random weights for each selected asset
    weights = np.random.rand(n_assets)
    weights = weights / sum(weights)  # Normalize weights so they sum to 1

    # Initialize portfolio return and variance
    portfolio_return = 0
    portfolio_variance = 0

    # Calculate portfolio return and variance
    for i in range(len(assets)):
        # Calculate portfolio return using the cleaned asset names for mus
        portfolio_return += weights[i] * mus.loc[assets[i]]

        for j in range(len(assets)):
            # Calculate portfolio variance using the cleaned asset names for cov matrix
            portfolio_variance += weights[i] * weights[j] * cov.loc[assets[i], assets[j]]

    # Add the mean (return) and variance for this portfolio to the list
    mean_variance_pairs.append([portfolio_return, portfolio_variance])

# Step 6: Convert the list of mean-variance pairs into a DataFrame for easier plotting
mean_variance_df = pd.DataFrame(mean_variance_pairs, columns=['Return', 'Variance'])

# Step 7: Create an interactive scatter plot with Plotly
fig = px.scatter(mean_variance_df, x='Variance', y='Return', color='Return',
                 color_continuous_scale='Viridis', title='Portfolio Optimization: Risk vs. Return',
                 labels={'Return': 'Portfolio Return', 'Variance': 'Portfolio Variance (Risk)'},
                 hover_data={'Return': True, 'Variance': True})

# Step 8: Show the interactive plot
fig.show()





NameError: name 'mus' is not defined

In [21]:
import numpy as np
import pandas as pd
import plotly.express as px

# =========================
# STEP 0: Ensure mus and cov are defined
# =========================

# mus: annualized returns for adjusted log variations
mus = (1 + df[adjusted_columns].mean()) ** 252 - 1

# cov: annualized covariance matrix for adjusted log variations
cov = df[adjusted_columns].cov() * 252

# =========================
# STEP 1: Clean the asset names
# =========================

# Clean asset names (remove 'LogVariationAjust ' prefix)
cleaned_assets = [col.split(' ')[-1] for col in df.columns if 'LogVariationAjust' in col]

# Update mus and cov indices/columns with cleaned names
mus.index = [col.split(' ')[-1] for col in mus.index]
cov.columns = [col.split(' ')[-1] for col in cov.columns]
cov.index = [col.split(' ')[-1] for col in cov.index]

# =========================
# STEP 2: Portfolio Simulation
# =========================

n_assets = 5        # Number of assets in each portfolio
n_portfolios = 10000  # Number of portfolios to generate
mean_variance_pairs = []  # To store portfolio return and variance

# Set seed for reproducibility
np.random.seed(75)

# =========================
# STEP 3: Generate random portfolios
# =========================

for _ in range(n_portfolios):
    # Randomly select n_assets from cleaned assets
    assets = np.random.choice(cleaned_assets, n_assets, replace=False)

    # Random weights normalized to sum to 1
    weights = np.random.rand(n_assets)
    weights /= sum(weights)

    # Portfolio return
    portfolio_return = sum(weights[i] * mus.loc[assets[i]] for i in range(n_assets))

    # Portfolio variance
    portfolio_variance = 0
    for i in range(n_assets):
        for j in range(n_assets):
            portfolio_variance += weights[i] * weights[j] * cov.loc[assets[i], assets[j]]

    # Append to list
    mean_variance_pairs.append([portfolio_return, portfolio_variance])

# =========================
# STEP 4: Convert to DataFrame for plotting
# =========================

mean_variance_df = pd.DataFrame(mean_variance_pairs, columns=['Return', 'Variance'])

# =========================
# STEP 5: Plot the portfolios
# =========================

fig = px.scatter(mean_variance_df, x='Variance', y='Return', color='Return',
                 color_continuous_scale='Viridis',
                 title='Portfolio Optimization: Risk vs. Return',
                 labels={'Return': 'Portfolio Return', 'Variance': 'Portfolio Variance (Risk)'},
                 hover_data={'Return': True, 'Variance': True})

fig.show()


In [23]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go

# Assuming mean_variance_pairs is already defined
mean_variance_pairs = np.array(mean_variance_pairs)

risk_free_rate = 0

fig = go.Figure()

# Scatter of portfolios colored by Sharpe ratio
fig.add_trace(go.Scatter(
    x=np.sqrt(mean_variance_pairs[:, 1]),  # Portfolio volatility
    y=mean_variance_pairs[:, 0],           # Portfolio return
    mode='markers',
    marker=dict(
        size=7,
        color=(mean_variance_pairs[:, 0] - risk_free_rate) / np.sqrt(mean_variance_pairs[:, 1]),  # Sharpe
        colorscale='RdBu',
        showscale=True,
        line=dict(width=1),
        colorbar=dict(title="Sharpe Ratio")
    )
))

# Layout
fig.update_layout(
    template='plotly_white',
    xaxis=dict(title='Annualised Risk (Volatility)'),
    yaxis=dict(title='Annualised Return'),
    title='Random Portfolios with Sharpe Ratio',
    width=850,
    height=500
)

# Automatically adjust axis ranges to your data
fig.update_xaxes(range=[0, np.sqrt(mean_variance_pairs[:,1]).max()*1.1])
fig.update_yaxes(range=[mean_variance_pairs[:,0].min()*0.9, mean_variance_pairs[:,0].max()*1.1])

fig.show()


In [27]:
print("Columns in df:", df.columns.tolist())
print("Index in mus:", mus.index.tolist())
print("Columns in cov:", cov.columns.tolist())
print("Index in cov:", cov.index.tolist())


Columns in df: ['Date', 'Close AAL', 'Close ABI.BR', 'Close AIR.PA', 'Close AMZN', 'Close DIS', 'Close ECOPETROL.CL', 'Close NFLX', 'Close SPG', 'Close UPS', 'Close USDCOP=X', 'High AAL', 'High ABI.BR', 'High AIR.PA', 'High AMZN', 'High DIS', 'High ECOPETROL.CL', 'High NFLX', 'High SPG', 'High UPS', 'High USDCOP=X', 'Low AAL', 'Low ABI.BR', 'Low AIR.PA', 'Low AMZN', 'Low DIS', 'Low ECOPETROL.CL', 'Low NFLX', 'Low SPG', 'Low UPS', 'Low USDCOP=X', 'Open AAL', 'Open ABI.BR', 'Open AIR.PA', 'Open AMZN', 'Open DIS', 'Open ECOPETROL.CL', 'Open NFLX', 'Open SPG', 'Open UPS', 'Open USDCOP=X', 'Volume AAL', 'Volume ABI.BR', 'Volume AIR.PA', 'Volume AMZN', 'Volume DIS', 'Volume ECOPETROL.CL', 'Volume NFLX', 'Volume SPG', 'Volume UPS', 'Volume USDCOP=X', 'LogVariation Close AAL', 'LogVariation Close ABI.BR', 'LogVariation Close AIR.PA', 'LogVariation Close AMZN', 'LogVariation Close DIS', 'LogVariation Close ECOPETROL.CL', 'LogVariation Close NFLX', 'LogVariation Close SPG', 'LogVariation Close U

In [28]:
from tqdm import tqdm
import numpy as np

n_assets = 5
n_portfolios = 10000

mean_variance_pairs = []
weights_list = []
tickers_list = []

np.random.seed(75)

tickers = mus.index.tolist()  # Clean asset names

for _ in tqdm(range(n_portfolios)):
    next_i = False
    while True:
        # Choose assets randomly from clean tickers
        assets = np.random.choice(tickers, n_assets, replace=False)

        # Random weights summing to 1
        weights = np.random.rand(n_assets)
        weights = weights / sum(weights)

        # Portfolio return and variance
        portfolio_E_Return = sum(weights[i] * mus.loc[assets[i]] for i in range(n_assets))
        portfolio_E_Variance = sum(weights[i] * weights[j] * cov.loc[assets[i], assets[j]]
                                   for i in range(n_assets) for j in range(n_assets))

        # Skip dominated portfolios
        for R, V in mean_variance_pairs:
            if (R > portfolio_E_Return) and (V < portfolio_E_Variance):
                next_i = True
                break
        if next_i:
            break

        # Store results
        mean_variance_pairs.append([portfolio_E_Return, portfolio_E_Variance])
        weights_list.append(weights)
        tickers_list.append(assets)
        break




100%|██████████| 10000/10000 [00:04<00:00, 2233.44it/s]


In [30]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from tqdm import tqdm

# ---- 1️⃣ Clean tickers from df (only LogVariationAjust columns) ----
cleaned_assets = [col.split(' ')[-1] for col in df.columns if 'LogVariationAjust' in col]

# Ensure mus and cov have matching indices
mus = mus.loc[cleaned_assets]
cov = cov.loc[cleaned_assets, cleaned_assets]

# ---- 2️⃣ Portfolio simulation ----
n_assets = 5       # assets per portfolio
n_portfolios = 5000  # number of portfolios (reduce first for speed)

mean_variance_pairs = []
weights_list = []
tickers_list = []

np.random.seed(75)

for _ in tqdm(range(n_portfolios)):
    # Randomly pick assets
    assets = np.random.choice(cleaned_assets, n_assets, replace=False)

    # Random weights
    weights = np.random.rand(n_assets)
    weights /= sum(weights)

    # Portfolio return & variance
    portfolio_return = np.sum([weights[i] * mus.loc[assets[i]] for i in range(n_assets)])
    portfolio_variance = 0
    for i in range(n_assets):
        for j in range(n_assets):
            portfolio_variance += weights[i] * weights[j] * cov.loc[assets[i], assets[j]]

    # Store results
    mean_variance_pairs.append([portfolio_return, portfolio_variance])
    weights_list.append(weights)
    tickers_list.append(assets)

# ---- 3️⃣ Convert to numpy array ----
mean_variance_pairs = np.array(mean_variance_pairs)

# ---- 4️⃣ Plotting ----
risk_free_rate = 0

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=np.sqrt(mean_variance_pairs[:,1]),  # volatility
    y=mean_variance_pairs[:,0],           # return
    mode='markers',
    marker=dict(
        size=7,
        line=dict(width=1),
        color=(mean_variance_pairs[:,0]-risk_free_rate)/np.sqrt(mean_variance_pairs[:,1]),  # Sharpe
        colorscale='RdBu',
        showscale=True,
        colorbar=dict(title='Sharpe Ratio')
    ),
    text=[f"{tickers_list[i]}<br>{weights_list[i].round(2)}" for i in range(len(tickers_list))]
))

fig.update_layout(
    template='plotly_white',
    title='Random Portfolios: Risk vs Return',
    xaxis_title='Annualized Risk (Volatility)',
    yaxis_title='Annualized Return',
    width=850,
    height=500
)

fig.update_xaxes(autorange=True)
fig.update_yaxes(autorange=True)

fig.show()



100%|██████████| 5000/5000 [00:02<00:00, 2186.28it/s]
